In [3]:
import glob
import string
import tensorflow as tf
from tensorflow.keras.layers import StringLookup
import keras_nlp
from keras_nlp.layers import StartEndPacker, TokenAndPositionEmbedding, TransformerDecoder
import numpy as np
np.set_printoptions(linewidth=200)

2024-02-06 10:56:47.426770: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-02-06 10:56:47.426833: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-02-06 10:56:47.428054: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-02-06 10:56:47.436868: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-02-06 10:56:49.504236: W tensorflow/compiler/tf2

Using TensorFlow backend


In [9]:
input_files = glob.glob('data/domains/*.txt')

print('Input files:', len(input_files))

Input files: 1


In [10]:
from tokenizers.trainers import BpeTrainer
trainer = BpeTrainer(special_tokens=["[PAD]", "[UNK]", "[STA]", "[END]"])

In [11]:
from tokenizers import Tokenizer
from tokenizers.models import BPE
tokenizer = Tokenizer(BPE(unk_token="[UNK]"))

In [12]:
tokenizer.train(input_files, trainer)

In [4]:
from collections import defaultdict
import gzip
word_freqs = defaultdict(int)

with gzip.open('data/domains/app.txt.gz', 'r') as f:

    for text in f:
        text = text.decode('utf-8')
        words_with_offsets = tokenizer.backend_tokenizer.pre_tokenizer.pre_tokenize_str(text)
        new_words = [word for word, offset in words_with_offsets]
        for word in new_words:
            word_freqs[word] += 1

print(word_freqs)

defaultdict(<class 'int'>, {'q': 1, 'Ċ': 534152, 'qa': 1, 'qaa': 1, 'qaabl': 1, 'qaaf': 1, 'qaagentsmith': 1, 'qaap': 1, 'qaas': 1, 'qab': 1, 'qabal': 1, 'qabas': 1, 'qabby': 1, 'qablannawm': 1, 'qaboolhai': 1, 'qaboom': 1, 'qabot': 1, 'qabrfinder': 1, 'qabuddy': 1, 'qacao': 1, 'qack': 1, 'qaclasses': 1, 'qactual': 1, 'qad': 1, 'qada': 1, 'qadam': 1, 'qadekvks': 1, 'qadense': 1, 'qado': 1, 'qadsan': 1, 'qadyane': 1, 'qae': 1, 'qaema': 1, 'qaf': 1, 'qafe': 1, 'qafeer': 1, 'qafela': 1, 'qafila': 1, 'qafla': 1, 'qaflow': 1, 'qag': 1, 'qagenda': 1, 'qagg': 1, 'qags': 1, 'qahal': 1, 'qahelper': 1, 'qahwa': 1, 'qaia': 1, 'qaim': 1, 'qainsurance': 1, 'qaiqai': 1, 'qair': 1, 'qaire': 1, 'qairn': 1, 'qairos': 1, 'qairy': 1, 'qaitbay': 1, 'qaiver': 1, 'qaj': 1, 'qaja': 1, 'qaku': 1, 'qal': 1, 'qala': 1, 'qalam': 1, 'qalamacademy': 1, 'qalboo': 1, 'qalbox': 1, 'qalbum': 1, 'qalbycommunity': 1, 'qalco': 1, 'qalenda': 1, 'qalender': 1, 'qalento': 1, 'qalert': 1, 'qalerts': 1, 'qali': 1, 'qalib': 1,

In [5]:
alphabet = []

for word in word_freqs.keys():
    for letter in word:
        if letter not in alphabet:
            alphabet.append(letter)
alphabet.sort()

print(alphabet)

['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', 'Ċ']


In [6]:
class SpecialTokens:
    PADDING = '[PAD]'
    UNKNOWN = '[UNK]'
    START = '[STA]'
    END = '[END]'
    
    Tokens = [PADDING, UNKNOWN, START, END]
    TokenDict = {PADDING: 0, UNKNOWN: 1, START: 2, END: 3}

In [7]:
vocab = SpecialTokens.Tokens + alphabet.copy()
vocab

['[PAD]',
 '[UNK]',
 '[STA]',
 '[END]',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z',
 'Ċ']

In [8]:
splits = {word: [c for c in word] for word in word_freqs.keys()}
merges = {}

In [9]:
def compute_pair_freqs(splits):
    pair_freqs = defaultdict(int)
    for word, freq in word_freqs.items():
        split = splits[word]
        if len(split) == 1:
            continue
        for i in range(len(split) - 1):
            pair = (split[i], split[i + 1])
            pair_freqs[pair] += freq
    return pair_freqs

In [10]:
pair_freqs = compute_pair_freqs(splits)

for i, key in enumerate(pair_freqs.keys()):
    print(f"{key}: {pair_freqs[key]}")
    if i >= 5:
        break

('q', 'a'): 570
('a', 'a'): 3384
('a', 'b'): 11792
('b', 'l'): 9460
('a', 'f'): 5799
('a', 'g'): 11617


In [11]:
def merge_pair(a, b, splits):
    for word in word_freqs:
        split = splits[word]
        if len(split) == 1:
            continue

        i = 0
        while i < len(split) - 1:
            if split[i] == a and split[i + 1] == b:
                split = split[:i] + [a + b] + split[i + 2 :]
            else:
                i += 1
        splits[word] = split
    return splits

In [14]:
vocab_size = 200

while len(vocab) < vocab_size:
    pair_freqs = compute_pair_freqs(splits)
    best_pair = ""
    max_freq = None
    for pair, freq in pair_freqs.items():
        if max_freq is None or max_freq < freq:
            best_pair = pair
            max_freq = freq
    splits = merge_pair(*best_pair, splits)
    merges[best_pair] = best_pair[0] + best_pair[1]
    vocab.append(best_pair[0] + best_pair[1])

In [13]:
vocab

['[PAD]',
 '[UNK]',
 '[STA]',
 '[END]',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z',
 'Ċ',
 'er',
 'in',
 'ar',
 'an',
 'al',
 'st',
 'en',
 'on',
 'or',
 'at',
 'et',
 're',
 'it',
 'ch',
 'es',
 'el',
 'ro',
 'ic',
 'as',
 'lo',
 'le',
 'ra',
 'co',
 'am',
 'th',
 'is',
 'ed',
 'ap',
 'ing',
 'li',
 'un',
 'ac',
 'de',
 'ot',
 'il',
 'us',
 'ur',
 'oo',
 'ad',
 'ri',
 'ent',
 'ec',
 'ay',
 'ab',
 'em',
 'ag',
 'om',
 'op',
 'ig',
 'im',
 'ut',
 'sh',
 'sp',
 'ion',
 'my',
 'ol',
 'ai',
 'pl',
 've',
 'oc',
 'vi',
 'di',
 'art',
 'ver',
 'up',
 'os',
 'ub',
 'eb',
 'um']

In [ ]:
merges

{('i', 'n'): 'in',
 ('a', 'r'): 'ar',
 ('a', 'n'): 'an',
 ('a', 'l'): 'al',
 ('s', 't'): 'st',
 ('e', 'n'): 'en',
 ('o', 'n'): 'on',
 ('o', 'r'): 'or',
 ('a', 't'): 'at',
 ('e', 't'): 'et',
 ('r', 'e'): 're',
 ('i', 't'): 'it',
 ('c', 'h'): 'ch',
 ('e', 's'): 'es',
 ('e', 'l'): 'el',
 ('r', 'o'): 'ro',
 ('i', 'c'): 'ic',
 ('a', 's'): 'as',
 ('l', 'o'): 'lo'}

In [34]:
TOTAL_ROWS = 500000
BATCH = 1024
EPOCHS = 100
STEP_EPOCHS = TOTAL_ROWS // BATCH
STEP_EPOCHS

488

In [41]:
MAX_SEQ_LEN = 20
MIN_SEQ_LEN = 5
EMBED_DIM = 96
NUM_HEADS = 24
FEED_FORWARD_DIM = 96



dataset = tf.data.TextLineDataset(input_files, compression_type='GZIP')
dataset = dataset.shuffle(buffer_size=1_000_000)
dataset = dataset.filter(lambda x: tf.strings.length(x) >= MIN_SEQ_LEN & tf.strings.length(x) <= MAX_SEQ_LEN)
dataset = dataset.batch(BATCH)

VOCAB = string.ascii_lowercase
VOCAB = SpecialTokens.Tokens + [c for c in VOCAB]

ids_from_chars = StringLookup(
    vocabulary=VOCAB,
    mask_token=SpecialTokens.PADDING,
    oov_token=SpecialTokens.UNKNOWN
)

chars_from_ids = StringLookup(
    vocabulary=VOCAB,
    invert=True,
    mask_token=SpecialTokens.PADDING,
    oov_token=SpecialTokens.UNKNOWN
)

start_token = ids_from_chars(tf.constant(SpecialTokens.START))
end_token = ids_from_chars(tf.constant(SpecialTokens.END))

print(start_token)

packer = StartEndPacker(
    MAX_SEQ_LEN,
    start_value=SpecialTokens.START,
    end_value=SpecialTokens.END,
    pad_value=SpecialTokens.PADDING,
    return_padding_mask=False
)


def prepare_lm_inputs_labels(text):
    chars = tf.strings.unicode_split(text, input_encoding='UTF-8')
    padded = packer(chars)
    tokens = ids_from_chars(padded)
    x = tokens[:, :-1]
    y = tokens[:, 1:]
    return x, y

text_ds = dataset.map(prepare_lm_inputs_labels, num_parallel_calls=tf.data.AUTOTUNE)
text_ds = text_ds.prefetch(tf.data.AUTOTUNE)
    
    
class CharTransformer(tf.keras.Model):
    def __init__(self, vocab_size:int, num_layers: int, embedding_dim: int, num_heads: int) -> None:
        super().__init__()
        self.embeddings = TokenAndPositionEmbedding(
            vocabulary_size=len(VOCAB),
            sequence_length=MAX_SEQ_LEN,
            embedding_dim=EMBED_DIM,
            mask_zero=True,
        )
        self.decoders = [TransformerDecoder(
            num_heads=NUM_HEADS, 
            intermediate_dim=FEED_FORWARD_DIM,
            dropout=0.1,
            activation='gelu'
            )
            for _ in range(num_layers)]
        self.dense = tf.keras.layers.Dense(vocab_size, activation='relu')
        
    def call(self, inputs):
        x = self.embeddings(inputs)
        for layer in self.decoders:
            x = layer(x)
        return self.dense(x)
      
model = CharTransformer(vocab_size=len(VOCAB), num_layers=2, embedding_dim=EMBED_DIM, num_heads=NUM_HEADS)


perplexity = keras_nlp.metrics.Perplexity(from_logits=True, mask_token_id=0)
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=[perplexity])


        

tf.Tensor(2, shape=(), dtype=int64)


In [42]:
model.fit(text_ds, epochs=EPOCHS, verbose=1)

Epoch 1/100
522/522 [==============================] - 108s 186ms/step - loss: 3.2127 - perplexity: 47.6775
Epoch 2/100


2024-02-06 09:39:03.793875: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 11649731160769717573
2024-02-06 09:39:03.794068: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 15495456782289674620
2024-02-06 09:39:03.794119: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 10014077403232570392
2024-02-06 09:39:03.794128: I tensorflow/core/framework/local_rendezvous.cc:425] Local rendezvous send item cancelled. Key hash: 5551772001302607106


522/522 [==============================] - 98s 186ms/step - loss: 2.9521 - perplexity: 112.2612
Epoch 3/100
522/522 [==============================] - 98s 187ms/step - loss: 2.9749 - perplexity: 134.9536
Epoch 4/100
522/522 [==============================] - 96s 183ms/step - loss: 2.9719 - perplexity: 267.6299
Epoch 5/100
522/522 [==============================] - 96s 183ms/step - loss: 2.9642 - perplexity: 208.6354
Epoch 6/100
522/522 [==============================] - 96s 183ms/step - loss: 2.9567 - perplexity: 175.2582
Epoch 7/100
522/522 [==============================] - 96s 183ms/step - loss: 2.9712 - perplexity: 129.9656
Epoch 8/100
522/522 [==============================] - 96s 183ms/step - loss: 2.9690 - perplexity: 126.1075
Epoch 9/100
522/522 [==============================] - 97s 185ms/step - loss: 2.9675 - perplexity: 99.6855
Epoch 10/100
522/522 [==============================] - 99s 189ms/step - loss: 2.9662 - perplexity: 82.9400
Epoch 11/100
522/522 [===================

KeyboardInterrupt: 

In [113]:
model.save('char_transformer_32_24h.keras')

In [37]:
prompt_packer = StartEndPacker(
    MAX_SEQ_LEN,
    start_value=SpecialTokens.START,
    pad_value=SpecialTokens.PADDING,
    return_padding_mask=False
)

In [38]:
def pack_prompt(prompt: str) -> tf.Tensor:
    chars = tf.strings.unicode_split(prompt, input_encoding='UTF-8')
    padded = prompt_packer(chars)
    tokens = ids_from_chars(padded)
    return tokens

In [39]:
def nextt(prompt, cache, index):
    logits = model(prompt)[:, index-1, :]
    # Ignore hidden states for now; only needed for contrastive search.
    hidden_states = None
    return logits, hidden_states, cache

In [40]:
prompt = ''
prompt_length = len(prompt)
prompt_tokens = pack_prompt([prompt])

sampler = keras_nlp.samplers.TopPSampler(0.5)
output_tokens = sampler(
    next=nextt,
    prompt=prompt_tokens,
    index=prompt_length+1,  # Start sampling immediately after the [BOS] token.
)
txt = chars_from_ids(output_tokens)
txt=tf.strings.reduce_join(txt, axis=-1).numpy()
print(f"Greedy search generated text: \n{txt}\n")

Greedy search generated text: 
[b'[STA][END][PAD]ii[END][PAD][END][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD]t[PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD][PAD]']

